# Learning materials, sources, references

## Python-specific

* https://docs.python.org/3/
    * https://docs.python.org/3/tutorial/ read through this
    * https://docs.python.org/3/library/ before you start implementing something or looking for pip packages
        * https://docs.python.org/3/library/asyncio.html asynchronous I/O
        * https://docs.python.org/3/library/ctypes.html to load C-like DLLs
        * https://docs.python.org/3/library/unittest.html one of testing options
    * https://docs.python.org/3/extending/ if you need C
    * https://docs.python.org/3/whatsnew/ there's a lot of important stuff posted there, actually (e.g. `match` keyword)
    * https://docs.python.org/3/reference/ in-depth about python itself
        * https://docs.python.org/3/reference/datamodel.html the most important part from that reference
* https://peps.python.org/
    * https://peps.python.org/pep-0008/ python style guide
    * https://peps.python.org/pep-0020 the zen of python
    * https://peps.python.org/pep-0257 docstrings
    * ~~https://peps.python.org/pep-0333 please no~~
* https://wiki.python.org/moin/FrontPage at the moment of writing, haven't read much of it

# Introduction
This notebook mostly features topics that are (IMO) overlooked.
* environment; there are a lot of choices for where to develop and where to deploy; I'll try to gather and classify as much viable options as I can.
* [typing](https://docs.python.org/3/library/typing.html); not everyone knows about annotations' existence (let alone that of the module); typing greatly enhances programmer's performance in any PL, and python is not an exception to that.
* [data model](https://docs.python.org/3/reference/datamodel.html); python has a very strict and simple data model behind it; once you understand it, things like ["why this attribute returns a totally different thing"](https://docs.python.org/3/reference/datamodel.html#object.__getattr__) will be more obvious.
* working with files; there are approaches beyond `open`+`.write`/`.read`.
* [asyncio](https://docs.python.org/3/library/asyncio.html); the only correct way to do IO, if you don't wish to waste time and memory.
* obscure new features; [`match`](https://docs.python.org/3/tutorial/controlflow.html#match-statements), [`Self`](https://peps.python.org/pep-0673/), [`type | type`](https://peps.python.org/pep-0604/), etc.; they are important, but not omnipresent as per their (in-language) [novelty](https://docs.python.org/3/whatsnew/index.html).
* [styling](https://peps.python.org/pep-0008/).
* testing (no link, because testing is quite diverse); not only unit tests; I'm still relatively incompetent at it, so things will be described from quite a limited perspective.

Most sections will eventually include "***prerequisites:***" part (things you need to know before looking into this section); things required are mostly found in the official tutorial.

# Environment

# [typing](https://docs.python.org/3/library/typing.html)
module: https://docs.python.org/3/library/typing.html  
relevant PEP: https://peps.python.org/pep-0484/

Even a dynamically typed language can sometimes, at least, declare types. Python has built-in support for that via annotations.

_**prerequisites:** [functions](https://docs.python.org/3/tutorial/controlflow.html#defining-functions)*_

***also mentioned here:** [`match`](https://docs.python.org/3/tutorial/controlflow.html#match-statements)*

In [3]:
import typing

## Declaring a type

### For a [variable](https://peps.python.org/pep-0526/)

In [4]:
num0: int
num0 = 1
num1: int = 1

### For a [function](https://docs.python.org/3/library/typing.html#callable)

In [5]:
def fn0(x: int) -> int:
    return x


fn1: typing.Callable[[int], int]
def fn1(x):
    return x

### Of a [generic](https://docs.python.org/3/library/typing.html#generics)

In [6]:
list0: list[int] = [0, 1]
dict0: dict[str, int] = {'0': 0, '1': 1}

### Of a [union](https://docs.python.org/3/library/stdtypes.html#types-union)
see also:
https://peps.python.org/pep-0604/
https://docs.python.org/3/library/typing.html#typing.Union

In [7]:
optional0: int | None = 0
optional1: typing.Union[int, None] = None
optional2: typing.Optional[int] = None
optional2 = -1

### example with [`match`](https://docs.python.org/3/tutorial/controlflow.html#match-statements)
though annotations don't usually influence anything during runtime, they make programming easier

In [8]:
def join(a: list[int] | set[str] | None) -> str | None:
    match a:
        case list():
            return ''.join(map(str, a))
        case set():
            return ''.join(a)
        case _:
            return None

result: tuple[str | None, str | None, str | None] = join([1, 2]), join({"1", "2"}), join(None)
result

('12', '12', None)

# [Data model](https://docs.python.org/3/reference/datamodel.html)
https://docs.python.org/3/reference/datamodel.html

***prerequisites:** [classes](https://docs.python.org/3/tutorial/classes.html)*

# Working with files
related tutorial section: https://docs.python.org/3/tutorial/inputoutput.html

There are a lot of ways, and directly using `open`+`.write`/`.read` is probably not fit for you task. So I decided not to link one specific external article to this section.

***prerequisites:** variables, [strings](https://docs.python.org/3/tutorial/introduction.html#strings)*

***also mentioned here:** [`with`](https://peps.python.org/pep-0343/)*

## [`pathlib`](https://docs.python.org/3/library/pathlib.html), [`pathlib.Path`](https://docs.python.org/3/library/pathlib.html#pathlib.Path)
One of the most overlooked python's modules is [`pathlib`](https://docs.python.org/3/library/pathlib.html).
Even more rare is the knowledge that [`Path`](https://docs.python.org/3/library/pathlib.html#pathlib.Path) objects have [`.open`](https://docs.python.org/3/library/pathlib.html#pathlib.Path.open), [`.write_*`](https://docs.python.org/3/library/pathlib.html#pathlib.Path.write_text) and [`.read_*`](https://docs.python.org/3/library/pathlib.html#pathlib.Path.read_text) methods.

In [12]:
import pathlib
tmp = pathlib.Path('tmp/')
tmp.mkdir(exist_ok=True)
example_txt = tmp / 'example.txt'
example_txt.touch(exist_ok=True)
example_txt.write_text(f'{2+3}\n{2*3}\n')
print(example_txt.read_text())

5
6



## File(-like) objects -- [streams](https://docs.python.org/3/library/io.html).
https://docs.python.org/3/library/io.html
Returned by `open(...)` and `pathlib.Path(...).open(...)`.

In [10]:
# avoid using `open` outside `with` (`with` better guarantees file's closure)
with open(example_txt, 'w') as f:
    f.write(f'{2+3}\n{2*3}\n')
with open(example_txt) as f:
    print(f.read())
with open(example_txt) as f:
    for line in f:
        print(line)

5
6

5

6



# The [`with`](https://peps.python.org/pep-0343/) statement.
~~AKA the reason I can't quit python~~

statement itself: https://docs.python.org/3/reference/compound_stmts.html#with  
relevant PEP: https://peps.python.org/pep-0343/  
the datamodel it represents: https://docs.python.org/3/reference/datamodel.html#context-managers

# [asyncio](https://docs.python.org/3/library/asyncio.html)
If you do anything with IO, you should probably do it **asynchronously**  
https://docs.python.org/3/library/asyncio.html

***prerequisites:** [functions](https://docs.python.org/3/tutorial/controlflow.html#defining-functions)*

***recommended before reading:** [classes](https://docs.python.org/3/tutorial/classes.html)*

***also mentioned here:** [`with`](https://peps.python.org/pep-0343/)*

In [11]:
import asyncio

## Background
The most prominent use of async IO is undoubtably anything that has to do with JavaScript (the web programming language).  
Due to \{1) limitations in performance 2) single-threaded environment (that can't allow any freezes) 3) constantly working with high-latency IO (because internet, client- and server-side) of high frequency (and high (number-wise) loads for servers)\}, JS kind of has to resort to using an event loop.  
All IO in JS is forced to be async.  
In browsers that is to prevent incompetent or malicious actors from killing your browser (or parts of it).  
In Node that is to prevent unnecessary blocking of code to achieve better performance.  
Ryan Dahl on Node.js:  
https://youtu.be/ztspvPYybIY  
https://youtu.be/jo_B4LTHi3I

## Level 0: working inside async framework
If you've ever worked with [`aiohttp`](https://docs.aiohttp.org/) or [`discord.py`](https://discordpy.readthedocs.io/)/[`disnake`](https://docs.disnake.dev/), you've probably encountered [`async`/`await` syntax](https://peps.python.org/pep-0492/).  
It may seems like these frameworks just make you put this magic words here and there.  
But there are reasons for both of these magic words.

### `async def` -- define an asynchronous function ([coroutine](https://docs.python.org/3/library/asyncio-task.html))
`async` here signals to python that the function might use `await`s inside it.  
Statements *inside* coroutines are guaranteed to happen in sequence with each other

### `await` -- virtually block on a future or on another coroutine and return result
While coroutine `await`s, other coroutines can be (and, probably, are) doing their own stuff.  
Any code between `await`s happens sequentially with all the other code, i.e. unlike [`threading`](https://docs.python.org/3/library/threading.html), `async` does not mix statements unpredictably.  
You always have the exclusive and direct control of data in code fragments where you don't `await`.  
Expression `(await f(...))` where `f` is defined as `async def f(...): ...` with `return x` evaluates to that `x`.  
Expression `(await future)` where `f` is `asyncio.Future` that has someone call `.set_result(x)` evaluates to that `x`.  

### [`async with` -- asynchronous context management](https://peps.python.org/pep-0492/#asynchronous-context-managers-and-async-with)
Same as `with`, but `async def __aenter__`/`async def __aexit__` instead of `def __enter__`/`def __exit__`.

### [`async for` -- asynchronous iteration](https://peps.python.org/pep-0492/#asynchronous-iterators-and-async-for)
Same as `for`, but `async def` instead of `def` for `yield`-based generators and `__aiter__`/`__anext__` instead of `__iter__`/`__next__` for iterators/iterables.

## Level 1: using [high-level APIs](https://docs.python.org/3/library/asyncio-api-index.html)

## Level 2: using [low-level APIs](https://docs.python.org/3/library/asyncio-llapi-index.html)

# Last section, for the empty cell(s) to not get stuck with previous sections